# 🗺️ k-NN Corse : Version Interactive avec Clic sur Carte

## 🎮 Mode d'emploi
1. Exécutez toutes les cellules
2. **Cliquez sur la carte** pour choisir un point
3. Ajustez k avec le curseur
4. Observez la classification en temps réel !

## 📦 Installation

In [ ]:
# Installation des bibliothèques
import sys
!{sys.executable} -m pip install ipyleaflet ipywidgets pandas numpy -q

In [ ]:
import pandas as pd
import numpy as np
import math
from collections import Counter
from ipyleaflet import Map, Marker, CircleMarker, Polyline, AwesomeIcon, LayerGroup
from ipywidgets import HTML, VBox, HBox, IntSlider, Output, Label
from IPython.display import display, clear_output

## 📊 Chargement des données

In [ ]:
# Charger les données
df = pd.read_csv('villages_corse.csv', sep='\t', encoding='utf-8')

def parse_coordinates(point_geo_str):
    try:
        parts = str(point_geo_str).split(',')
        lat = float(parts[0].strip())
        lon = float(parts[1].strip())
        return lat, lon
    except:
        return None, None

df[['latitude', 'longitude']] = df['Point_Geo'].apply(
    lambda x: pd.Series(parse_coordinates(x))
)

df = df.dropna(subset=['latitude', 'longitude'])
df['dept_simple'] = df['Code Département'].apply(lambda x: '2A' if str(x) == '2A' else '2B')

print(f"✅ {len(df)} villages chargés")
print(f"   - Corse du Sud (2A) : {len(df[df['dept_simple']=='2A'])}")
print(f"   - Haute-Corse (2B) : {len(df[df['dept_simple']=='2B'])}")

## 🧮 Fonctions k-NN

In [ ]:
def haversine_distance(lat1, lon1, lat2, lon2):
    """Calcule la distance en km entre deux points GPS."""
    R = 6371
    lat1_rad = math.radians(lat1)
    lat2_rad = math.radians(lat2)
    delta_lat = math.radians(lat2 - lat1)
    delta_lon = math.radians(lon2 - lon1)
    
    a = math.sin(delta_lat/2)**2 + math.cos(lat1_rad) * math.cos(lat2_rad) * math.sin(delta_lon/2)**2
    c = 2 * math.asin(math.sqrt(a))
    
    return R * c

def knn_classify(test_lat, test_lon, df, k=5):
    """Classifie un point avec k-NN."""
    distances = []
    for idx, row in df.iterrows():
        dist = haversine_distance(test_lat, test_lon, row['latitude'], row['longitude'])
        distances.append({
            'village': row['Nom français'],
            'nom_corse': row['Nom corse'],
            'departement': row['dept_simple'],
            'latitude': row['latitude'],
            'longitude': row['longitude'],
            'distance': dist
        })
    
    dist_df = pd.DataFrame(distances).sort_values('distance')
    neighbors = dist_df.head(k)
    votes = Counter(neighbors['departement'])
    prediction = votes.most_common(1)[0][0]
    
    return prediction, neighbors, votes

## 🗺️ Carte Interactive

**Instructions :**
- 🖱️ **Cliquez sur la carte** pour placer un point
- 🎚️ **Ajustez k** avec le curseur
- 👁️ La classification se met à jour automatiquement

In [ ]:
# Créer la carte
m = Map(center=(42.15, 9.05), zoom=9, scroll_wheel_zoom=True)

# Couches pour les éléments dynamiques
test_point_layer = LayerGroup()
neighbors_layer = LayerGroup()
lines_layer = LayerGroup()

m.add_layer(test_point_layer)
m.add_layer(neighbors_layer)
m.add_layer(lines_layer)

# Afficher quelques villages de référence
sample_villages = df.sample(n=min(50, len(df)), random_state=42)
for idx, row in sample_villages.iterrows():
    color = 'red' if row['dept_simple'] == '2A' else 'blue'
    circle = CircleMarker(
        location=(row['latitude'], row['longitude']),
        radius=3,
        color=color,
        fill_color=color,
        fill_opacity=0.4,
        weight=1
    )
    m.add_layer(circle)

# Widget pour k
k_slider = IntSlider(
    value=5,
    min=1,
    max=20,
    step=1,
    description='k:',
    continuous_update=False
)

# Zone de résultats
result_output = Output()
info_html = HTML(value="<p style='font-size:16px; padding:10px; background:#f0f0f0; border-radius:5px;'>👆 <b>Cliquez sur la carte pour classifier un point</b></p>")

# Variable globale pour stocker les coordonnées
current_coords = {'lat': None, 'lon': None}

def update_classification(lat, lon, k):
    """Met à jour la classification et la visualisation."""
    # Effacer les couches précédentes
    test_point_layer.clear_layers()
    neighbors_layer.clear_layers()
    lines_layer.clear_layers()
    
    # Classification
    prediction, neighbors, votes = knn_classify(lat, lon, df, k=k)
    
    # Couleur selon prédiction
    color = 'red' if prediction == '2A' else 'blue'
    dept_name = 'Corse du Sud (2A)' if prediction == '2A' else 'Haute-Corse (2B)'
    
    # Marqueur du point test
    icon = AwesomeIcon(
        name='star',
        marker_color='darkred' if prediction == '2A' else 'darkblue',
        icon_color='white'
    )
    test_marker = Marker(location=(lat, lon), icon=icon, draggable=False)
    test_point_layer.add_layer(test_marker)
    
    # Afficher les k plus proches voisins
    for idx, neighbor in neighbors.iterrows():
        n_color = 'red' if neighbor['departement'] == '2A' else 'blue'
        
        # Marqueur du voisin
        n_marker = CircleMarker(
            location=(neighbor['latitude'], neighbor['longitude']),
            radius=8,
            color=n_color,
            fill_color=n_color,
            fill_opacity=0.7,
            weight=2
        )
        neighbors_layer.add_layer(n_marker)
        
        # Ligne vers le voisin
        line = Polyline(
            locations=[
                (lat, lon),
                (neighbor['latitude'], neighbor['longitude'])
            ],
            color=n_color,
            weight=2,
            opacity=0.5
        )
        lines_layer.add_layer(line)
    
    # Afficher les résultats
    with result_output:
        clear_output(wait=True)
        print(f"📍 Coordonnées : ({lat:.4f}, {lon:.4f})")
        print(f"🔢 k = {k}")
        print(f"\n🎯 Prédiction : {dept_name}")
        print(f"📊 Votes : 2A={votes.get('2A', 0)}, 2B={votes.get('2B', 0)}")
        print(f"\n🏘️ Les {k} plus proches villages :")
        print(neighbors[['village', 'nom_corse', 'departement', 'distance']].to_string(index=False))
    
    # Mettre à jour l'info
    info_html.value = f"<div style='font-size:16px; padding:10px; background:{'#ffebee' if prediction=='2A' else '#e3f2fd'}; border-radius:5px; border-left: 4px solid {color};'><b>Classification : {dept_name}</b><br>Votes : 2A={votes.get('2A', 0)}, 2B={votes.get('2B', 0)}</div>"

def handle_click(**kwargs):
    """Gestionnaire de clic sur la carte."""
    if kwargs.get('type') == 'click':
        coords = kwargs.get('coordinates')
        lat, lon = coords
        current_coords['lat'] = lat
        current_coords['lon'] = lon
        update_classification(lat, lon, k_slider.value)

def on_k_change(change):
    """Gestionnaire de changement de k."""
    if current_coords['lat'] is not None:
        update_classification(current_coords['lat'], current_coords['lon'], change['new'])

# Connecter les événements
m.on_interaction(handle_click)
k_slider.observe(on_k_change, names='value')

# Afficher l'interface
display(VBox([
    info_html,
    HBox([Label('Nombre de voisins (k):'), k_slider]),
    m,
    result_output
]))

## 🎯 Points d'intérêt à tester

Essayez de cliquer sur ces zones :

- **Ajaccio** : (41.9267, 8.7369) - Capitale 2A
- **Bastia** : (42.7028, 9.4500) - Préfecture 2B
- **Corte** : (42.3062, 9.1509) - Centre de la Corse
- **Frontière approximative** : Zone entre 42.0 et 42.3 latitude

### Questions à explorer :
1. 🤔 Où se situe la "frontière" k-NN entre les deux départements ?
2. 📊 Comment k influence-t-il la classification près de cette frontière ?
3. 🏔️ Y a-t-il des zones ambiguës où le résultat change souvent ?

## 💡 Mode manuel (si la carte ne fonctionne pas)

Si le clic sur carte ne fonctionne pas, utilisez cette cellule :

In [ ]:
# Mode manuel : entrez les coordonnées
test_lat = 42.3  # Modifiez ici
test_lon = 9.15  # Modifiez ici
k = 5

prediction, neighbors, votes = knn_classify(test_lat, test_lon, df, k=k)
dept_name = 'Corse du Sud (2A)' if prediction == '2A' else 'Haute-Corse (2B)'

print(f"📍 Point : ({test_lat}, {test_lon})")
print(f"🎯 Prédiction : {dept_name}")
print(f"📊 Votes : {dict(votes)}")
print(f"\n🏘️ Les {k} plus proches villages :")
print(neighbors[['village', 'nom_corse', 'departement', 'distance']].to_string(index=False))

## 📝 Notes techniques

Cette version utilise **ipyleaflet** qui offre une vraie interactivité bidirectionnelle entre Python et JavaScript dans Jupyter.

**Avantages :**
- ✅ Clic directement sur la carte
- ✅ Mise à jour en temps réel
- ✅ Curseur interactif pour k
- ✅ Pas besoin de recharger

**Prérequis :**
- Jupyter Notebook ou JupyterLab
- Extension widgets activée : `jupyter nbextension enable --py widgetsnbextension`